In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
from sklearn.model_selection import train_test_split
from keras.models import Sequential
from keras.layers import Dense, LSTM

In [2]:
df = pd.read_csv('/content/food_delivery_dataset.csv')
df.head(10)

ID Delivery_person_ID  Delivery_person_Age  Delivery_person_Ratings  \
0  4607     INDORES13DEL02                   37                      4.9   
1  B379     BANGRES18DEL02                   34                      4.5   
2  5D6D     BANGRES19DEL01                   23                      4.4   
3  7A6A    COIMBRES13DEL02                   38                      4.7   
4  70A2     CHENRES12DEL01                   32                      4.6   
5  9BB4      HYDRES09DEL03                   22                      4.8   
6  95B4   RANCHIRES15DEL01                   33                      4.7   
7  9EB2      MYSRES15DEL02                   35                      4.6   
8  1102      HYDRES05DEL02                   22                      4.8   
9  CDCD      DEHRES17DEL01                   36                      4.2   

   Restaurant_latitude  Restaurant_longitude  Delivery_location_latitude  \
0            22.745049             75.892471                   22.765049   
1            12.913041             77.683237                   13.043041   
2            12.914264             77.678400                   12.924264   
3            11.003669             76.976494                   11.053669   
4            12.972793             80.249982                   13.012793   
5            17.431668             78.408321                   17.461668   
6            23.369746             85.339820                   23.479746   
7            12.352058             76.606650                   12.482058   
8            17.433809             78.386744                   17.563809   
9            30.327968             78.046106                   30.397968   

   Delivery_location_longitude Type_of_order Type_of_vehicle  Time_taken(min)  
0                    75.912471        Snack      motorcycle                24  
1                    77.813237        Snack         scooter                33  
2                    77.688400       Drinks      motorcycle                26  
3                    77.026494       Buffet      motorcycle                21  
4                    80.289982        Snack         scooter                30  
5                    78.438321       Buffet      motorcycle                26  
6                    85.449820         Meal         scooter                40  
7                    76.736650         Meal      motorcycle                32  
8                    78.516744       Buffet      motorcycle                34  
9                    78.116106        Snack      motorcycle                46

In [3]:
df.isnull().sum()

ID                             0
Delivery_person_ID             0
Delivery_person_Age            0
Delivery_person_Ratings        0
Restaurant_latitude            0
Restaurant_longitude           0
Delivery_location_latitude     0
Delivery_location_longitude    0
Type_of_order                  0
Type_of_vehicle                0
Time_taken(min)                0
dtype: int64

**Find the distance btw two locations using Haversine Formula**

In [4]:
R = 6371  #The Earth's radius (in km)

def deg_to_rad(degrees):
    return degrees * (np.pi/180)

# The haversine formula
def dist_calculate(lat1, lon1, lat2, lon2):
    d_lat = deg_to_rad(lat2-lat1)
    d_lon = deg_to_rad(lon2-lon1)
    a1 = np.sin(d_lat/2)**2 + np.cos(deg_to_rad(lat1))
    a2 = np.cos(deg_to_rad(lat2)) * np.sin(d_lon/2)**2
    a = a1 * a2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1-a))
    return R * c

# Create distance column & calculate the distance
df['distance'] = np.nan

df['distance'] = df.apply(lambda row: dist_calculate(row['Restaurant_latitude'],
                                                     row['Restaurant_longitude'],
                                                     row['Delivery_location_latitude'],
                                                     row['Delivery_location_longitude']),
                         axis=1)


In [5]:
figure = px.violin(df, x="distance", y="Time_taken(min)",
                   box=True, points="all", title="Violin Plot of Time Taken Over Distance")
figure.show()

In [6]:
figure_line = px.line(df, x="Delivery_person_Age", y="Time_taken(min)",
                      title="Time Taken Over Delivery Partner Age")
figure_line.show()

In [7]:
figure_box = px.box(data_frame=df,
                    x="Delivery_person_Ratings",
                    y="Time_taken(min)",
                    color="distance",
                    title="Box Plot of Time Taken by Delivery Partner Ratings",
                    points="all")

figure_box.show()

In [8]:
fig = px.box(df,
             x="Type_of_vehicle",
             y="Time_taken(min)",
             color="Type_of_order",
             title = "Relationship Between Type of Vehicle and Type of Order")
fig.show()

In [9]:
x = np.array(df[["Delivery_person_Age",
                   "Delivery_person_Ratings",
                   "distance"]])
y = np.array(df[["Time_taken(min)"]])
xtrain, xtest, ytrain, ytest = train_test_split(x, y,
                                                test_size=0.20,
                                                random_state=33)

In [10]:
model = Sequential()
model.add(LSTM(128, return_sequences=True, input_shape= (xtrain.shape[1], 1)))
model.add(LSTM(64, return_sequences=False))
model.add(Dense(25))
model.add(Dense(1))
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm (LSTM)                 (None, 3, 128)            66560     
                                                                 
 lstm_1 (LSTM)               (None, 64)                49408     
                                                                 
 dense (Dense)               (None, 25)                1625      
                                                                 
 dense_1 (Dense)             (None, 1)                 26        
                                                                 
Total params: 117619 (459.45 KB)
Trainable params: 117619 (459.45 KB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


In [11]:
model.compile(optimizer='adam', loss='mean_squared_error')
model.fit(xtrain, ytrain, batch_size=1, epochs=9)

Epoch 1/9
36474/36474 [==============================] - 182s 5ms/step - loss: 69.3301
Epoch 2/9
36474/36474 [==============================] - 176s 5ms/step - loss: 64.7517
Epoch 3/9
36474/36474 [==============================] - 176s 5ms/step - loss: 62.2548
Epoch 4/9
36474/36474 [==============================] - 175s 5ms/step - loss: 61.1974
Epoch 5/9
36474/36474 [==============================] - 175s 5ms/step - loss: 60.2028
Epoch 6/9
36474/36474 [==============================] - 176s 5ms/step - loss: 60.2341
Epoch 7/9
36474/36474 [==============================] - 175s 5ms/step - loss: 59.7387
Epoch 8/9
36474/36474 [==============================] - 175s 5ms/step - loss: 59.3627
Epoch 9/9
36474/36474 [==============================] - 176s 5ms/step - loss: 58.9320


In [12]:
print("Food Delivery Time Prediction System")
a = int(input("Delivery Partner Age: "))
b = float(input("Previous Delivery Ratings: "))
c = int(input("Total Distance: "))

features = np.array([[a, b, c]])
print("Delivery Time Prediction in Minutes = ", model.predict(features))

Food Delivery Time Prediction System
Delivery Partner Age: 24
Previous Delivery Ratings: 4.0
Total Distance: 7
1/1 [==============================] - 1s 648ms/step
Delivery Time Prediction in Minutes =  [[40.237476]]
